In [4]:
import pandas as pd
import numpy as np

In [5]:
a = pd.read_csv("Entradas_de_extranjeros_a_Colombia_20241017.csv")

In [6]:
a.columns = ["Year","Mes","Nationality","ISO_CODE","Female","Masculine","Indefinite","total","latlonraw"]
a['latlona'] = a['latlonraw'].apply(lambda x: x.replace("(","").replace(")","").split(","))
a['latlon'] = a['latlona'].apply(lambda x: f'[{x[1]},{x[0].replace(",","")}]')

In [7]:
ab = a.groupby(["latlon"])['total'].sum().reset_index()

In [8]:
ac = a.groupby(['latlon','Nationality'])['total'].sum().reset_index()
countries = ac.groupby(['latlon']).apply(lambda x: x.sort_values('total', ascending=False)[['Nationality','total']].head(1)).reset_index()

In [9]:
ad = pd.merge(ab,countries[['Nationality','latlon']],left_on='latlon',right_on='latlon')[['latlon','total','Nationality']]

In [10]:
ad['color'] = np.where(ad['Nationality'].isin(['Estados Unidos de América','Venezuela']),ad['Nationality'],'"#51d1f5"')
ad['color'] = np.where(ad['color']=='Estados Unidos de América','"#a60be3"',ad['color'])
ad['color'] = np.where(ad['color']=='Venezuela','"#fcba03"',ad['color'])

In [11]:
print(ad[['latlon','color','total']].to_json(orient='records').replace('"', "").replace("\\", '"'))


[{latlon:[-67.47535,6.18189],color:"#fcba03",total:830},{latlon:[-67.483929,6.185799],color:"#fcba03",total:36845},{latlon:[-67.927521,3.866713],color:"#fcba03",total:4046},{latlon:[-69.941278,-4.197703],color:"#51d1f5",total:66431},{latlon:[-69.945098,-4.223468],color:"#51d1f5",total:15677},{latlon:[-70.356599,-3.790089],color:"#51d1f5",total:22},{latlon:[-70.740253,7.088729],color:"#fcba03",total:91888},{latlon:[-71.983761,12.165168],color:"#fcba03",total:192},{latlon:[-71.989035,12.2205723],color:"#fcba03",total:2},{latlon:[-72.129330,11.360009],color:"#fcba03",total:927116},{latlon:[-72.405710,8.364293],color:"#fcba03",total:28331},{latlon:[-72.409396,8.36068],color:"#fcba03",total:155532},{latlon:[-72.453226,7.818934],color:"#fcba03",total:2420426},{latlon:[-72.462544,7.916725],color:"#fcba03",total:71749},{latlon:[-72.507910,7.927209],color:"#fcba03",total:68642},{latlon:[-72.919681,11.528919],color:"#fcba03",total:3903},{latlon:[-73.183637,7.128456],color:"#a60be3",total:42468},

In [12]:
import pycountry

In [15]:
unique_countries = a['ISO_CODE'].unique()

In [16]:
country_list = list(pycountry.countries)

In [17]:
list_of_countries = {int(country.numeric):country.name for country in country_list if int(country.numeric) in unique_countries}

In [19]:
a['Country'] = a['ISO_CODE'].map(list_of_countries)

In [21]:
a_last_4_years = a[a['Year'].isin([2012,2022])].dropna(subset='Country')

In [24]:
a_last_4_years

Year        Mes                                        Nationality  \
1       2012      Enero                                            Albania   
2       2012      Enero                                           Alemania   
3       2012      Enero                                           Alemania   
4       2012      Enero                                           Alemania   
5       2012      Enero                                           Alemania   
...      ...        ...                                                ...   
127162  2022  Diciembre                           República Árabe de Yemen   
127163  2022  Diciembre                                           Zimbabue   
127164  2022  Diciembre           Anguila/Territorio Británico de Ultramar   
127165  2022  Diciembre  Islas Turcas y Caicos/Territorio Británico de ...   
127166  2022  Diciembre  Islas Turcas y Caicos/Territorio Británico de ...   

        ISO_CODE  Female  Masculine  Indefinite  total  \
1              8       1          2         NaN      3   
2            276      11         16         NaN     27   
3            276       1          1         NaN      2   
4            276      63        102         NaN    165   
5            276      22         23         NaN     45   
...          ...     ...        ...         ...    ...   
127162       887       0          3         NaN      3   
127163       716       1          2         NaN      3   
127164       660       1          2         NaN      3   
127165       796       1          0         NaN      1   
127166       796       1          0         NaN      1   

                     latlonraw                  latlona  \
1        (4.697144,-74.140516)   [4.697144, -74.140516]   
2       (-4.197703,-69.941278)  [-4.197703, -69.941278]   
3         (0.25129,-76.875963)    [0.25129, -76.875963]   
4        (0.814836,-77.662532)   [0.814836, -77.662532]   
5       (10.408582,-75.538003)  [10.408582, -75.538003]   
...                        ...                      ...   
127162   (4.697144,-74.140516)   [4.697144, -74.140516]   
127163   (4.697144,-74.140516)   [4.697144, -74.140516]   
127164   (3.541112,-76.384584)   [3.541112, -76.384584]   
127165  (10.445761,-75.516429)  [10.445761, -75.516429]   
127166   (6.171601,-75.427454)   [6.171601, -75.427454]   

                        latlon                   Country  
1        [-74.140516,4.697144]                   Albania  
2       [-69.941278,-4.197703]                   Germany  
3         [-76.875963,0.25129]                   Germany  
4        [-77.662532,0.814836]                   Germany  
5       [-75.538003,10.408582]                   Germany  
...                        ...                       ...  
127162   [-74.140516,4.697144]                     Yemen  
127163   [-74.140516,4.697144]                  Zimbabwe  
127164   [-76.384584,3.541112]                  Anguilla  
127165  [-75.516429,10.445761]  Turks and Caicos Islands  
127166   [-75.427454,6.171601]  Turks and Caicos Islands  

[25046 rows x 12 columns]

In [26]:
a_last_4_years_sum = a_last_4_years[a_last_4_years['Country'].isin(['Argentina'])].groupby(['latlon','Year'])['total'].sum().reset_index()

In [35]:
def sort_df(x):
    x_copy = x.copy().sort_values('Year')
    x_copy['pct_change'] = x_copy['total'].pct_change()*100
    return x_copy[['Year','total','pct_change']]

In [36]:
a_last_4_years_sum_pct_chamge = a_last_4_years_sum.groupby(['latlon']).apply(sort_df).reset_index()
# a_last_4_years_sum_pct_chamge = a_last_4_years_sum_pct_chamge[a_last_4_years_sum_pct_chamge['Total']>10000]

In [38]:
a_last_4_years_sum_pct_chamge.dropna()

latlon  level_1  Year  total   pct_change
3    [-69.941278,-4.197703]        3  2022     67   -40.178571
6     [-70.740253,7.088729]        6  2022      4   -20.000000
8    [-72.129330,11.360009]        8  2022     74   -87.414966
11    [-72.453226,7.818934]       11  2022    227   -71.265823
14    [-72.507910,7.927209]       14  2022    131   156.862745
17    [-73.183637,7.128456]       17  2022     68    33.333333
19    [-74.140516,4.697144]       19  2022  76289    -8.108792
21   [-74.213989,11.247723]       21  2022      5    25.000000
24   [-74.776708,10.886611]       24  2022    763    59.958071
26    [-75.427454,6.171601]       26  2022   6955    97.922595
28   [-75.516429,10.445761]       28  2022   9398   -28.056342
30   [-75.538003,10.408582]       30  2022     53   -91.506410
32    [-75.736532,4.815061]       32  2022    138   102.941176
34    [-75.766298,4.452882]       34  2022    206  1960.000000
36    [-76.384584,3.541112]       36  2022   2013    37.782341
38     [-76.875963,0.25129]       38  2022     32    -3.030303
41    [-77.346578,8.635765]       41  2022     12   -93.181818
44    [-77.662532,0.814836]       44  2022    746   -69.846403
47   [-81.702563,12.586067]       47  2022   1653   -67.537313
49  [-81.703935,12.5744111]       49  2022      6   -14.285714

In [127]:
df = a_last_4_years_sum_pct_chamge[a_last_4_years_sum_pct_chamge['Año']==2022].sort_values("pct_change").dropna().sort_values("pct_change")
df['Country'] = df['Country'].apply(lambda x: f"'{x}'")

In [141]:
df_s = pd.DataFrame(df.iloc[-1]).T

In [147]:
df_s[['Country','pct_change','geojson']].to_json(orient='records').replace('"', "")

"[{Country:'Dominican Republic',pct_change:795.8054032094,geojson:{\\type\\: \\FeatureCollection\\, \\crs\\: {\\type\\: \\name\\, \\properties\\: {\\name\\: \\EPSG:4326\\}}, \\features\\: [{\\type\\: \\Feature\\, \\properties\\: {\\province_name\\: \\DISTRITO NACIONAL\\, \\municipalities\\: 1}, \\geometry\\: {\\type\\: \\MultiPolygon\\, \\coordinates\\: [[[[-69.97480276252212, 18.54526772958401], [-69.97461923376578, 18.5452532026515], [-69.97430012584512, 18.54526127550891], [-69.97404818021208, 18.54527959559406], [-69.97370266224225, 18.54531754558477], [-69.97347992686066, 18.54535878415818], [-69.97261315304421, 18.54564741124598], [-69.97225842141503, 18.54578191938727], [-69.97203887655368, 18.54578304957636], [-69.97196703212629, 18.54575545864071], [-69.97184040642772, 18.54565876108952], [-69.97176789131014, 18.5455345237538], [-69.97175854348734, 18.54547235787938], [-69.97175354518413, 18.54543911720048], [-69.97179414595628, 18.54529404206139], [-69.97189018051675, 18.5451

In [3]:
a

NameError: name 'a' is not defined